In [18]:
import pandas as pd
import numpy as np

In [19]:
df = pd.read_csv('non_skill_builder_data_new.csv')
df.columns

Index(['order_id', 'assignment_id', 'user_id', 'assistment_id', 'problem_id',
       'original', 'correct', 'attempt_count', 'ms_first_response',
       'tutor_mode', 'answer_type', 'sequence_id', 'student_class_id',
       'position', 'type', 'base_sequence_id', 'skill_id', 'skill_name',
       'teacher_id', 'school_id', 'hint_count', 'hint_total', 'overlap_time',
       'template_id', 'answer_id', 'answer_text', 'first_action',
       'bottom_hint', 'opportunity', 'opportunity_original'],
      dtype='object')

The dataset description can be found [here](https://sites.google.com/site/assistmentsdata/home/2009-2010-assistment-data).

Some key columns are explained:

- skill_id

    ID of the skill associated with the problem.

    For the skill builder dataset, different skills for the same data record are in different rows. This means if a student answers a multi skill question, this record is duplicated several times, and each duplication is tagged with one of the multi skills.

    For the non skill builder dataset, different skills for the same data record are in the same row, separated with comma.

- skill_name

    Skill name associated with the problem.

    For the skill builder dataset, different skills for the same data record are in different rows. This means if a student answers a multi skill question, this record is duplicated several times, and each duplication is tagged with one of the multi skills.

    For the non skill builder dataset, different skills for the same data record are in the same row, separated with comma.





In [20]:
df = df.sort_values(by='order_id')

print(df['ms_first_response'].describe())
# assert df['ms_first_response'].is_monotonic_increasing

target_cols = ['skill_id', 'problem_id']

df_cleaned = df.dropna(subset=target_cols)

print(
    f'total {len(df) - len(df_cleaned)} of the original {len(df)} have been removed ({len(df_cleaned) / len(df)} percentage is saved)\n')

df = df_cleaned

count    6.031200e+05
mean     5.777229e+04
std      1.646758e+06
min     -9.406091e+06
25%      8.452000e+03
50%      2.049700e+04
75%      4.792200e+04
max      8.643416e+08
Name: ms_first_response, dtype: float64
total 0 of the original 603128 have been removed (1.0 percentage is saved)



In [21]:
# df['skill_id'] = df['skill_id'].astype(int)
# df['problem_id'] = df['problem_id'].astype(int)
# #check if we have to remap skill id and question id
# sid_set = df['skill_id'].unique()
# print(sid_set.max())
# print(sid_set.min())
# print(len(sid_set))
# qid_set = df['problem_id'].unique()
#
# print(qid_set.max())
# print(qid_set.min())
# print(len(qid_set))



In [22]:
#remap the qid and sid
qs_mapping = {}
sq_mapping = {}
qid_to_name = {}
sid_to_name = {}
for idx, row in df.iterrows():

    order_id = row['order_id']

    if pd.isna(row['skill_name']):
        row['skill_name'] = 'nan'

    s_name_set = row['skill_name'].split(',')

    qid = row['problem_id']
    import ast

    sid_set = ast.literal_eval(row['skill_id'])
    if isinstance(sid_set,int):
        sid_set = {sid_set}
    if len(sid_set) >= 3:
        print(sid_set)
        print(s_name_set)
    for idx, sid in enumerate(sid_set):
        s_name = s_name_set[idx]
        if s_name == '':
            s_name = 'nan'
        if sid not in sq_mapping.keys():
            sq_mapping[sid] = set()
        sq_mapping[sid].add(qid)

        if qid not in qs_mapping.keys():
            qs_mapping[qid] = set()
        qs_mapping[qid].add(sid)

        sid_to_name[sid] = s_name
        qid_to_name[qid] = qid

qid_set = qs_mapping.keys()
sid_set = sq_mapping.keys()

qid_to_index = {}
sid_to_index = {}

for index, q in enumerate(qid_set):
    qid_to_index[q] = index + 1

for index, s in enumerate(sid_set):
    sid_to_index[s] = index + 1

qs_matrix = np.zeros([len(qid_to_index) + 1, len(sid_to_index) + 1], dtype=int)
for q, s_list in qs_mapping.items():
    for s in s_list:
        qs_matrix[qid_to_index[q]][sid_to_index[s]] = 1
np.save('preprocessed/qs_matrix.npy', qs_matrix)


(69, 92, 97)
['Multiplication Whole Numbers', 'Pattern Finding ', '']
(98, 99, 332)
['', '', 'Finding Slope from Graph']
(98, 99, 105)
['', '', '']
(24, 42, 95, 312)
['Congruence', 'Perimeter of a Polygon', 'Substitution', 'Equation Solving More Than Two Steps']
(99, 104, 349)
['', '', 'Parallel and Perpendicular Slopes']
(99, 105, 332)
['', '', 'Finding Slope from Graph']
(90, 103, 349)
['Picking Equation and Inequality from Choices', 'Point Plotting', 'Parallel and Perpendicular Slopes']
(99, 105, 332)
['', '', 'Finding Slope from Graph']
(99, 105, 332)
['', '', 'Finding Slope from Graph']
(99, 105, 332)
['', '', 'Finding Slope from Graph']
(99, 105, 332)
['', '', 'Finding Slope from Graph']
(99, 105, 332)
['', '', 'Finding Slope from Graph']
(99, 105, 332)
['', '', 'Finding Slope from Graph']
(99, 105, 332)
['', '', 'Finding Slope from Graph']
(99, 105, 332)
['', '', 'Finding Slope from Graph']
(99, 105, 332)
['', '', 'Finding Slope from Graph']
(99, 105, 332)
['', '', 'Finding Slop

In [23]:
# Merge the dictionaries

merged_dict = {(sid, s_index): (sid, s_index, sid_to_name[sid]) for sid, s_index in sid_to_index.items()}

# Sort the merged dictionary by value of 'b'
sorted_keys = sorted(merged_dict, key=lambda x: x[1])

with open('preprocessed/sid_remapping.txt', 'w') as f:
# Print the triple elements
    for key in sorted_keys:
        original_id, remapped_id, s_name = merged_dict[key]
        print(type(s_name))
        print(str(remapped_id) + ' , ' + str(original_id) + ' , ' + s_name + '\n')
        f.write(str(remapped_id) + ' , ' + str(original_id) + ' , ' + s_name + '\n')



<class 'str'>
1 , 231 , Symbolization

<class 'str'>
2 , 100 , nan

<class 'str'>
3 , 93 , nan

<class 'str'>
4 , 35 , Effect of Changing Dimensions of a Shape Prportionally

<class 'str'>
5 , 101 , nan

<class 'str'>
6 , 58 , Addition Whole Numbers

<class 'str'>
7 , 5 , Number Line

<class 'str'>
8 , 102 , nan

<class 'str'>
9 , 69 , Multiplication Whole Numbers

<class 'str'>
10 , 92 , Pattern Finding 

<class 'str'>
11 , 97 , nan

<class 'str'>
12 , 99 , nan

<class 'str'>
13 , 105 , nan

<class 'str'>
14 , 98 , nan

<class 'str'>
15 , 332 , Finding Slope from Graph

<class 'str'>
16 , 103 , Point Plotting

<class 'str'>
17 , 106 , Graph Shape

<class 'str'>
18 , 8 , Scatter Plot

<class 'str'>
19 , 52 , Ordering Whole Numbers

<class 'str'>
20 , 166 , Algebraic Solving

<class 'str'>
21 , 226 , Substitution

<class 'str'>
22 , 279 , Multiplication and Division Integers

<class 'str'>
23 , 24 , Congruence

<class 'str'>
24 , 42 , Perimeter of a Polygon

<class 'str'>
25 , 95 , Subs

In [24]:
print(qid_to_index)
from collections import OrderedDict

qid_to_index = OrderedDict(sorted(qid_to_index.items(), key=lambda x: x[1]))

with open('preprocessed/qid_remapping.txt', 'w') as f:
    for original_id, remapped_id in qid_to_index.items():
        f.write(str(remapped_id) + ' , ' + str(original_id) + ' , ' + str(original_id) + '\n')

qid_to_index

{12914: 1, 15320: 2, 14529: 3, 1159: 4, 1647: 5, 2705: 6, 2186: 7, 1653: 8, 2345: 9, 2196: 10, 3522: 11, 1613: 12, 2343: 13, 4572: 14, 9033: 15, 1989: 16, 4247: 17, 4052: 18, 2716: 19, 2713: 20, 2714: 21, 2715: 22, 2726: 23, 2712: 24, 2724: 25, 9789: 26, 9790: 27, 9791: 28, 9792: 29, 1063: 30, 2719: 31, 5: 32, 4084: 33, 4081: 34, 4082: 35, 4083: 36, 4541: 37, 14512: 38, 15203: 39, 12937: 40, 13894: 41, 15811: 42, 14768: 43, 14589: 44, 13386: 45, 13629: 46, 13495: 47, 14436: 48, 13795: 49, 14595: 50, 13506: 51, 14519: 52, 15816: 53, 20927: 54, 13485: 55, 13639: 56, 13340: 57, 14757: 58, 13575: 59, 13655: 60, 15661: 61, 68275: 62, 12519: 63, 13568: 64, 4468: 65, 34105: 66, 34339: 67, 33735: 68, 34182: 69, 34183: 70, 12931: 71, 13169: 72, 14524: 73, 78: 74, 75: 75, 76: 76, 77: 77, 12524: 78, 13707: 79, 15529: 80, 13339: 81, 14553: 82, 13698: 83, 15154: 84, 13703: 85, 13118: 86, 13490: 87, 13441: 88, 14516: 89, 15240: 90, 12638: 91, 12513: 92, 13902: 93, 13502: 94, 13486: 95, 14349: 96, 13

OrderedDict([(12914, 1),
             (15320, 2),
             (14529, 3),
             (1159, 4),
             (1647, 5),
             (2705, 6),
             (2186, 7),
             (1653, 8),
             (2345, 9),
             (2196, 10),
             (3522, 11),
             (1613, 12),
             (2343, 13),
             (4572, 14),
             (9033, 15),
             (1989, 16),
             (4247, 17),
             (4052, 18),
             (2716, 19),
             (2713, 20),
             (2714, 21),
             (2715, 22),
             (2726, 23),
             (2712, 24),
             (2724, 25),
             (9789, 26),
             (9790, 27),
             (9791, 28),
             (9792, 29),
             (1063, 30),
             (2719, 31),
             (5, 32),
             (4084, 33),
             (4081, 34),
             (4082, 35),
             (4083, 36),
             (4541, 37),
             (14512, 38),
             (15203, 39),
             (12937, 40),
      

In [25]:

print(df.columns)
df_user_groups = df.groupby('user_id')
seqs = {}

# remap question id
import datetime


for uid, df_user in df_user_groups:
    assert uid == df_user['user_id'].iloc[0]
    # are the interactions following the time order

    q_seq = df_user['problem_id'].tolist()
    r_seq = df_user['correct'].tolist()
    t_seq = df_user['ms_first_response'].tolist()
    seqs[uid] = {"question": q_seq, "result": r_seq, 'time': t_seq}

import json

with open('preprocessed/user_seq.json', 'w') as f:
    json.dump(seqs, f)


Index(['order_id', 'assignment_id', 'user_id', 'assistment_id', 'problem_id',
       'original', 'correct', 'attempt_count', 'ms_first_response',
       'tutor_mode', 'answer_type', 'sequence_id', 'student_class_id',
       'position', 'type', 'base_sequence_id', 'skill_id', 'skill_name',
       'teacher_id', 'school_id', 'hint_count', 'hint_total', 'overlap_time',
       'template_id', 'answer_id', 'answer_text', 'first_action',
       'bottom_hint', 'opportunity', 'opportunity_original'],
      dtype='object')
